# Correlation Power Analysis (Brier et al. 2004) - Evolution Plot


#### Learning goals
- Learn how to detect how many traces are needed for a CPA attack
- Learn what an Evolution Plot is

#### References
- `lascar.ScoreProgressionOutputMethod`

In [4]:
%load_ext autoreload
%autoreload 2

import os
import random

import lascar
import numpy as np
import plotly.graph_objects as pgo
from cwtoolbox import CaptureDevice


The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


## How many traces are needed?

To detect the minimal number of required traces for a CPA attack we have to determine when the _correct_ key guess is distinguishable from all _incorrect_ ones.

An _Evolution Plot_ can visualize this.

In [9]:
class EvolutionOutputMethod(lascar.ScoreProgressionOutputMethod):
    def _finalize(self):
        scores = np.array(list(self.scores.values())[0]).T
        fig = pgo.Figure()
        for guess, score in zip(self.engines[0]._guess_range, scores):
            fig.add_trace(pgo.Scatter(x=self.steps, y=score, name=str(guess)))
        fig.show()


<div style="border: 3px solid plum; border-radius: 5px; padding: 5px; width: calc(100% - 20px);">
<div class="h2" style="font-variant: all-small-caps;">Exercise 1</div>

Create an Evolution Plot using Lascar's `CpaEngine`.

Hints:
- `lascar.Session` takes an argument to store intermediate values in regular steps. Append `output_steps=range(0, len(data), 100)` to the list of parameters when creating the session.

</div>

In [14]:
capture_device = CaptureDevice.create("CWLITEXMEGA")
capture_device.compile(file=os.path.abspath("../lecture_3/sbox_lookup.c"))
capture_device.flash()

data = capture_device.capture(
    number_of_traces=1000,
    input=lambda _: list(random.randbytes(16)),
)

XMEGA Programming flash...
XMEGA Reading flash...
Verified flash OK, 2513 bytes


100%|██████████| 1000/1000 [00:08<00:00, 111.92it/s]


In [15]:
def selection_function(value, guess):
    return lascar.tools.aes.sbox[value[0] ^ guess] & 0x80 == 0

def selection_function_gen(n):
    return lambda v,g: lascar.tools.aes.sbox[v[n] ^ g] & 0x80 == 0



trace = lascar.TraceBatchContainer(data["trace"], data["input"])

#for i in range(16):
engine = lascar.CpaEngine(
    selection_function=selection_function_gen(0),
    guess_range=range(256),
)

session = lascar.Session(
    trace,
    engine=engine,
    output_method=EvolutionOutputMethod(engine),
    output_steps=range(0, len(data), 2)
).run(batch_size="auto")

2023-12-07 15:53:17,114 - lascar.session - INFO - Session Session: 1000 traces, 3 engines, batch_size=43832, leakage_shape=(1368,)
INFO:lascar.session:Session Session: 1000 traces, 3 engines, batch_size=43832, leakage_shape=(1368,)
Session |  0%||0 trc/1000 | (3 engines, batch_size=43832, leakage_shape=(1368,)) |ETA:  --:--:--


/usr/local/lib/python3.10/dist-packages/lascar/engine/cpa_engine.py:91: RuntimeWarning:

invalid value encountered in divide

Session |  0%||2 trc/1000 | (3 engines, batch_size=43832, leakage_shape=(1368,)) |ETA:   0:02:27
Session |  1%||14 trc/1000 | (3 engines, batch_size=43832, leakage_shape=(1368,)) |ETA:   0:02:25
Session |  2%||26 trc/1000 | (3 engines, batch_size=43832, leakage_shape=(1368,)) |ETA:   0:00:15
Session |  3%||38 trc/1000 | (3 engines, batch_size=43832, leakage_shape=(1368,)) |ETA:   0:00:15
Session |  5%||52 trc/1000 | (3 engines, batch_size=43832, leakage_shape=(1368,)) |ETA:   0:00:11
Session |  6%||64 trc/1000 | (3 engines, batch_size=43832, leakage_shape=(1368,)) |ETA:   0:00:10
Session |  7%||76 trc/1000 | (3 engines, batch_size=43832, leakage_shape=(1368,)) |ETA:   0:00:09
Session |  8%||82 trc/1000 | (3 engines, batch_size=43832, leakage_shape=(1368,)) |ETA:   0:00:10
Session |  9%||90 trc/1000 | (3 engines, batch_size=43832, leakage_shape=(1368,)) |ETA:   0